In [1]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm

### Tree and dataframe setup

In [2]:
# generate a random tree
NSPECIES = 80
TREE = toytree.rtree.bdtree(
    ntips=NSPECIES,
    seed=666,
).mod.node_scale_root_height(1.0)

# node idxs that delimit several distinct clades on this tree
CLADES = [152, 153, 154, 155]

# draw and color the four major clades
TREE.draw(
    layout='d', 
    width=500,
    tip_labels=False,
    edge_colors=TREE.get_edge_values_mapped({
        j: toytree.colors[i] for i, j in enumerate(CLADES)
    }),
    scalebar=True,
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t3b1cabe6510a49c5955a99b41fa01913" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0

In [3]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in CLADES}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])

In [4]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 3.0
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33

# 4 different clade effects on rate of RI (used for partial-pooling data)
𝜓_0_mean = 1.0
𝜓_0_std = 0.1
𝜓_1_mean = 0.5
𝜓_1_std = 0.05
𝜓_2_mean = -0.5
𝜓_2_std = 0.05
𝜓_3_mean = -1.0
𝜓_3_std = 0.1

In [5]:
# species dataframe
SPECIES_DATA = pd.DataFrame({
    "gidx": gidx,
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_0_mean, 𝜓_0_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_1_mean, 𝜓_1_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_2_mean, 𝜓_2_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_3_mean, 𝜓_3_std, len(gidx[gidx == 3])),
    ]),
})
SPECIES_DATA.head()

gidx         b       psi     psi_x
0     0  2.570468 -0.236524  0.997529
1     0  3.292698 -0.624017  0.863576
2     0  2.936227 -0.612795  0.956139
3     0  2.746916 -0.234236  1.115301
4     0  2.767121  0.031270  0.981499

### Generate crossing data

In [6]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(NSPECIES), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [(get_dist(TREE, i, j) / 2) for (i, j) in zip(a, b)],
})

DATA['b'] = np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)
DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)
DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])
# DATA['error'] = np.random.normal(0.0, 𝜎_std, DATA.shape[0])

# get logits
DATA['logit_b'] = (
    1 / (1 + np.exp(-(DATA.b * DATA.dist ** 2 + DATA.intercept * DATA.dist)))
)
DATA['logit'] = (
    1 / (1 + np.exp(-(DATA.velo * DATA.dist ** 2 + DATA.intercept * DATA.dist)))
)
DATA['logit_x'] = (
    1 / (1 + np.exp(-(DATA.velo_x * DATA.dist ** 2 + DATA.intercept * DATA.dist)))
)

# get RI estimates
DATA['RI_pooled'] = np.random.binomial(n=1, p=DATA.logit_b / DATA.logit_b.max())
DATA['RI_unpooled'] = np.random.binomial(n=1, p=DATA.logit / DATA.logit.max())
DATA['RI_partpooled'] = np.random.binomial(n=1, p=DATA.logit_x / DATA.logit_x.max())

DATA.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      0      1  0.073376  2.881579  2.021039  4.742684   0.023752  0.504314   
1      0      2  0.089748  2.638508  1.789189  4.592176   0.074466  0.506983   
2      0      3  0.129770  3.113867  2.643107  5.226697   0.055129  0.514894   
3      0      4  0.144542  3.059197  2.853944  5.038226   0.059521  0.518121   
4      0      5  0.144542  2.620887  2.866354  4.699434   0.059066  0.515818   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.503156  0.506819          0            0              0  
1  0.505273  0.510916          1            1              0  
2  0.512913  0.523775          0            1              0  
3  0.517051  0.528435          0            0              1  
4  0.517099  0.526655          0            0              0

In [7]:
NSAMPLES = 2000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0     60     63  0.578689  2.921440  2.625589  1.913308   0.044766  0.731892   
1     46     74  0.592720  3.287330  3.246154  1.886728   0.043472  0.765067   
2     23     30  0.438896  2.615066  2.010742  4.803178   0.057368  0.629231   
3     61     71  0.592720  3.160457  2.911351  1.778620   0.020785  0.754479   
4     23     34  0.590047  3.069562  2.832857  4.990309   0.039344  0.748739   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.712010  0.660750          1            1              1  
1  0.762457  0.665657          0            0              0  
2  0.601689  0.721198          1            0              1  
3  0.737909  0.654116          1            1              1  
4  0.732920  0.853287          1            1              1

### Visualize data

In [8]:
def logit_plot(dist, logit, RI):
    canvas = toyplot.Canvas(width=500, height=250)
    ax0 = canvas.cartesian(
        label="pooled data (function)",
        xlabel="Genetic dist.",
        ylabel="Logit function",
        grid=(1, 2, 0),
    )
    ax1 = canvas.cartesian(
        label="pooled data (observation)",
        xlabel="Genetic dist.",
        ylabel="RI",
        grid=(1, 2, 1),
    )

    # points are jittered on x-axis for visibility
    ax0.scatterplot(
        dist,
        logit,
        size=5,
        opacity=0.33,
        color=toyplot.color.Palette()[0],
    );
    ax1.scatterplot(
        dist,
        RI,
        size=10,
        opacity=0.2,
        marker="|",
        mstyle={
            "stroke": toyplot.color.Palette()[1],
            "stroke-width": 3,
        },
    );
    return canvas, (ax0, ax1)

In [9]:
logit_plot(SAMPLE.dist, SAMPLE.logit_b, SAMPLE.RI_pooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t1a0de7836f224f70bd50c82c863ffc0d" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%

In [10]:
logit_plot(SAMPLE.dist, SAMPLE.logit, SAMPLE.RI_unpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t55ab18c16da74ef9970528f7e0b5c43e" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);st

In [11]:
logit_plot(SAMPLE.dist, SAMPLE.logit_x, SAMPLE.RI_partpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t4962de08a6554a31b26635ddbb2cb528" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacit

### Define models

In [12]:
def pooled_logistic(x, y, **kwargs):
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = (𝛽 * x ** 2) + 𝛼 * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [13]:
def unpooled_logistic(x, y, idx0, idx1, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0.values)
        sidx1 = pm.Data("spp_idx1", idx1.values)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = ((𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x ** 2) + 𝛼 * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [14]:
def partpooled_logistic(x, y, idx0, idx1, gidx, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0)
        sidx1 = pm.Data("spp_idx1", idx1)
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=4)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=4)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        
        # linear model prediction
        effect = ((𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x ** 2) + 𝛼 * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood (normal distributed errors)
        y = pm.Bernoulli("y", p=logit, observed=y)

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Functions to plot results

In [15]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [16]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

In [17]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=10000,
    draws=10000,
    target_accept=0.99,
    return_inferencedata=False,
    progressbar=True,
)

### Run three datasets under pooled model

In [18]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_pooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 416 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [44]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_unpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 352 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_partpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


### Run three datasets under unpooled model

In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_pooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 14372 seconds.


In [31]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_unpooled_data  = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 18129 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [33]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_partpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 14133 seconds.
The number of effective samples is smaller than 25% for some parameters.


### Run three datasets under partpooled model

In [36]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_pooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 6540 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [38]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_unpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 8877 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [19]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_partpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 7561 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [20]:
partpooled_model_partpooled_data['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝜓_mean[0]    1.577  2.248  -2.620    5.783      0.029    0.021    5821.0   
𝜓_mean[1]    0.590  2.254  -3.522    4.943      0.029    0.021    5900.0   
𝜓_mean[2]    0.119  2.255  -4.205    4.257      0.029    0.021    5893.0   
𝜓_mean[3]   -0.648  2.253  -4.897    3.542      0.029    0.021    5875.0   
𝜓_offset[0]  0.172  0.966  -1.702    1.938      0.005    0.005   37948.0   
...            ...    ...     ...      ...        ...      ...       ...   
logit[1995]  0.737  0.029   0.683    0.792      0.000    0.000   35488.0   
logit[1996]  0.566  0.019   0.531    0.601      0.000    0.000   42619.0   
logit[1997]  0.635  0.056   0.529    0.742      0.000    0.000   40312.0   
logit[1998]  0.672  0.058   0.567    0.787      0.000    0.000   33788.0   
logit[1999]  0.971  0.016   0.943    0.996      0.000    0.000   35423.0   

              ess_sd  ess_bulk  ess_tail  r_hat  
𝜓_mean[0]     5821.0    5821.0   11576.0    1.0  
𝜓_mean[1]     5900.0    5900.0   11948.0    1.0  
𝜓_mean[2]     5893.0    5892.0   12005.0    1.0  
𝜓_mean[3]     5875.0    5875.0   11874.0    1.0  
𝜓_offset[0]  18701.0   37957.0   27832.0    1.0  
...              ...       ...       ...    ...  
logit[1995]  34896.0   36272.0   29696.0    1.0  
logit[1996]  42619.0   42615.0   30446.0    1.0  
logit[1997]  40312.0   40542.0   30218.0    1.0  
logit[1998]  33287.0   33950.0   29849.0    1.0  
logit[1999]  35423.0   35694.0   32764.0    1.0  

[2170 rows x 11 columns]

In [21]:
toytrace(partpooled_model_partpooled_data['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="tf3a3dc3a623c44a2923e20d4273d0a6d" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 109.31144327345719 149.92163009404388 L 112.75274182625054 149.92163009404388 L 116.19404037904391 149.92163009404388 L 119.63533893183728 149.68652037617554 L 123.07663748463065 149.76489028213166 L 126.517936037424 149.68652037617554 L 129.95923459021736 149.52978056426332 L 133.40053314301073 149.45141065830722 L 136.8418316958041 149.29467084639498 L 140.28313024859744 149.52978056426332 L 143.72442880139081 149.05956112852664 L 147.16572735418418 148.51097178683386 L 150.60702590697753 148.1974921630094 L 154.0483244597709 146.63009404388714 L 157.48962301256427 147.72727272727272 L 160.9309215653576 146.1598746081505 L 164.37222011815098 144.9843260188088 L 167.81351867094432 143.96551724137933 L 171.2548172237377 142.94670846394985 L 174.69611577653106 141.30094043887146 L 178.13741432932443 139.96865203761755 L 181.57871288211777 135.65830721003135 L 185.02001143491117 136.6771159874608 L 188.46130998770454 133.69905956112854 L 191.90260854049788 129.93730407523512 L 195.34390709329125 126.09717868338558 L 198.7852056460846 121.23824451410658 L 202.22650419887793 122.0219435736677 L 205.66780275167133 116.37931034482757 L 209.10910130446467 110.8934169278997 L 212.55039985725804 108.5423197492163 L 215.99169841005138 100.94043887147335 L 219.43299696284478 101.25391849529782 L 222.87429551563812 96.55172413793103 L 226.3155940684315 88.32288401253918 L 229.75689262122486 85.81504702194357 L 233.19819117401823 77.74294670846395 L 236.63948972681158 74.3730407523511 L 240.08078827960492 73.66771159874608 L 243.52208683239832 71.08150470219435 L 246.96338538519163 65.20376175548589 L 250.40468393798503 60.50156739811913 L 253.8459824907784 61.44200626959248 L 257.28728104357174 60.26645768025079 L 260.7285795963651 54.937304075235105 L 264.1698781491585 54.54545454545454 L 267.6111767019518 58.93416927899686 L 271.05247525474516 57.75862068965517 L 274.49377380753856 62.14733542319749 L 277.9350723603319 63.793103448275865 L 281.37637091312524 66.45768025078371 L 284.8176694659186 66.92789968652038 L 288.258968018712 65.9090909090909 L 291.7002665715053 71.78683385579937 L 295.1415651242987 76.48902821316615 L 298.58286367709206 87.6959247648903 L 302.0241622298854 85.03134796238244 L 305.4654607826788 94.04388714733543 L 308.9067593354722 95.92476489028212 L 312.34805788826554 101.01880877742946 L 315.78935644105894 106.6614420062696 L 319.2306549938523 109.95297805642633 L 322.6719535466456 110.81504702194358 L 326.113252099439 115.83072100313478 L 329.55455065223236 119.59247648902823 L 332.9958492050257 126.41065830721003 L 336.43714775781905 129.31034482758622 L 339.8784463106124 131.6614420062696 L 343.31974486340573 134.48275862068965 L 346.7610434161992 135.10971786833855 L 350.2023419689925 139.96865203761755 L 353.64364052178587 142.24137931034483 L 357.0849390745792 143.1818181818182 L 360.5262376273726 143.80877742946706 L 363.96753618016595 144.82758620689654 L 367.40883473295935 145.06269592476488 L 370.85013328575263 146.1598746081505 L 374.29143183854603 146.9435736677116 L 377.73273039133943 147.96238244514106 L 381.1740289441328 147.5705329153605 L 384.6153274969261 148.51097178683386 L 388.0566260497195 148.04075235109718 L 391.49792460251285 148.90282131661442 L 394.93922315530625 149.21630094043886 L 398.3805217080996 149.60815047021944 L 401.82182026089293 149.76489028213166 L 405.26311881368633 149.68652037617554 L 408.7044173664797 150.0 L 412.1457159

In [22]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t30700951d89049e6ab25009c508136e5" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -1 0 1 2 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [53]:
stats.linregress(partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

LinregressResult(slope=0.8996203153771799, intercept=-0.4165166943064579, rvalue=0.9550366624726686, pvalue=6.172818681506917e-43, stderr=0.03162267701105342)

In [23]:
draw_velocity_dists(partpooled_model_partpooled_data['trace'], baseline = 1.2);

<svg class="toyplot-canvas-Canvas" height="300.0px" id="te262965b34b944c7ae45f02a062cb15f" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <polygon points="187.24342587510387,250.0 188.38238116929475,250.0 189.52133646348562,250.0 190.66029175767648,250.0 191.79924705186735,250.0 192.93820234605823,250.0 194.07715764024908,250.0 195.21611293443993,250.0 196.3550682286308,250.0 197.4940235228217,250.0 198.63297881701257,250.0 199.77193411120345,250.0 200.9108894053943,250.0 202.04984469958518,250.0 203.18879999377606,250.0 204.3277552879669,250.0 205.46671058215782,250.0 206.60566587634864,250.0 207.74462117053952,250.0 208.88357646473042,250.0 210.02253175892128,250.0 211.16148705311213,250.0 212.300442347303,250.0 213.43939764149388,250.0 214.57835293568476,250.0 215.71730822987564,250.0 216.85626352406646,250.0 217.99521881825734,250.0 219.13417411244825,250.0 220.2731294066391,250.0 221.41208470082995,250.0 222.55103999502083,250.0 223.6899952892117,250.0 224.8289505834026,250.0 225.96790587759347,250.0 227.10686117178432,250.0 228.24581646597517,250.0 229.38477176016607,250.0 230.52372705435695,250.0 231.66268234854778,250.0 232.80163764273865,250.0 233.94059293692953,250.0 235.0795482311204,250.0 236.21850352531126,250.0 237.35745881950214,250.0 238.496414113693,250.0 239.6353694078839,250.0 240.77432470207478,250.0 241.9132799962656,250.0 243.0522352904565,250.0 244.19119058464736,250.0 245.33014587883824,250.0 246.46910117302915,250.0 247.60805646721997,250.0 248.74701176141082,250.0 249.88596705560172,250.0 251.0249223497926,250.0 252.16387764398345,250.0 253.30283293817433,250.0 254.44178823236518,250.0 255.58074352655606,250.0 256.71969882074694,250.0 257.8586541149378,250.0 258.9976094091287,250.0 260.13656470331955,250.0 261.2755199975104,250.0 262.4144752917013,250.0 263.55343058589216,250.0 264.692385880083,250.0 265.83134117427386,250.0 266.97029646846477,250.0 268.1092517626557,250.0 269.24820705684647,250.0 270.3871623510373,250.0 271.5261176452282,250.0 272.66507293941913,250.0 273.80402823361,250.0 274.94298352780083,250.0 276.0819388219917,250.0 277.2208941161826,250.0 278.3598494103735,250.0 279.49880470456435,250.0 280.6377599987552,250.0 281.77671529294605,250.0 282.91567058713696,250.0 284.0546258813278,250.0 285.19358117551866,250.0 286.33253646970957,250.0 287.4714917639004,250.0 288.6104470580913,250.0 289.7494023522822,250.0 290.88835764647297,250.0 292.0273129406639,250.0 293.1662682348548,250.0 294.30522352904563,250.0 295.44417882323654,250.0 296.58313411742733,250.0 297.72208941161824,250.0 298.86104470580915,250.0 300.0,250.0 300.0,249.04818266753261 298.86104470580915,248.88573994988792 297.72208941161824,248.69976180335456 296.58313411742733,248.48761385798713 295.44417882323654,248.24649960641986 294.30522352904563,247.97347271563203 293.1662682348548,247.6654539121979 292.0273129406639,247.31925281903418 290.88835764647297,246.93159506156817 289.7494023522822,246.49915488306857 288.6104470580913,246.01859341224818 287.4714917639004,245.4866026113895 286.33253646970957,244.8999548010387 285.19358117551866,244.25555750936374 284.0546258813278,243.5505132329446 282.91567058713696,242.78218352419998 281.77671529294605,241.94825664277167 280.6377599987552,241.04681782861707 279.49880470456435,240.07642107857953 278.3598494103735,239.03616114161682 277.2208941161826,237.92574429683853 276.0819388219917,236.74555634939293 274.94298352780083,235.496726178379 273.80402823361,234.18118310439917 272.66507293941913,232.8017063176537 271.5261176452282,231.361964625369 270.3871623510373,229.8665448435819

### Assess model fit

In [30]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val

In [31]:
def aicm(mean, variance):
    return 2*mean - 2*variance

In [32]:
rmse(unpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi'])

0.9292188416833755

In [33]:
rmse(partpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

0.6797919539022527

In [34]:
aicm(unpooled_sub['trace']['𝜓'].mean(), unpooled_sub['trace']['𝜓'].var())

-23.831186286890336

In [35]:
# Raftery et al. (2007) holds that this value is better.  R+M disagree?
aicm(partpooled_sub['trace']['𝜓'].mean(), partpooled_sub['trace']['𝜓'].var())

-11.997795212343398

In [45]:
az_pooled_model_pooled_data = az.from_pymc3(trace = pooled_model_pooled_data['trace'], 
                                            model = pooled_model_pooled_data['model'])
az_pooled_model_unpooled_data = az.from_pymc3(trace = pooled_model_unpooled_data['trace'], 
                                            model = pooled_model_unpooled_data['model'])
az_pooled_model_partpooled_data = az.from_pymc3(trace = pooled_model_partpooled_data['trace'], 
                                            model = pooled_model_partpooled_data['model'])
az_unpooled_model_pooled_data = az.from_pymc3(trace = unpooled_model_pooled_data['trace'], 
                                            model = unpooled_model_pooled_data['model'])
az_unpooled_model_unpooled_data = az.from_pymc3(trace = unpooled_model_unpooled_data['trace'], 
                                            model = unpooled_model_unpooled_data['model'])
az_unpooled_model_partpooled_data = az.from_pymc3(trace = unpooled_model_partpooled_data['trace'], 
                                            model = unpooled_model_partpooled_data['model'])
az_partpooled_model_pooled_data = az.from_pymc3(trace = partpooled_model_pooled_data['trace'], 
                                            model = partpooled_model_pooled_data['model'])
az_partpooled_model_unpooled_data = az.from_pymc3(trace = partpooled_model_unpooled_data['trace'], 
                                            model = partpooled_model_unpooled_data['model'])
az_partpooled_model_partpooled_data = az.from_pymc3(trace = partpooled_model_partpooled_data['trace'], 
                                            model = partpooled_model_partpooled_data['model'])

### Compare models with different datasets

In [46]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "pooled_model_unpooled_data": az_pooled_model_unpooled_data, 
            "pooled_model_partpooled_data": az_pooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo      weight  \
pooled_model_pooled_data        0 -702.378  2.06549        0    0.765127   
pooled_model_partpooled_data    1 -725.945  1.98954  23.5669    0.230179   
pooled_model_unpooled_data      2 -773.488  2.05086  71.1099  0.00469398   

                                   se      dse warning loo_scale  
pooled_model_pooled_data      25.3411        0   False       log  
pooled_model_partpooled_data  24.9677  32.0085   False       log  
pooled_model_unpooled_data    24.6806   32.626   False       log

In [47]:
az.compare({"unpooled_model_pooled_data": az_unpooled_model_pooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo      weight  \
unpooled_model_pooled_data        0 -701.455  20.3711        0    0.736811   
unpooled_model_partpooled_data    1  -722.43  24.5418  20.9746    0.259126   
unpooled_model_unpooled_data      2 -773.176  15.8619  71.7212  0.00406259   

                                     se      dse warning loo_scale  
unpooled_model_pooled_data      24.3943        0   False       log  
unpooled_model_partpooled_data  25.4337  32.1201   False       log  
unpooled_model_unpooled_data    25.4249  32.4747   False       log

In [48]:
az.compare({"partpooled_model_pooled_data": az_partpooled_model_pooled_data,
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo       weight  \
partpooled_model_pooled_data        0  -703.59  29.7137        0     0.542956   
partpooled_model_partpooled_data    1 -708.151  19.3844  4.56058      0.45692   
partpooled_model_unpooled_data      2 -776.279  26.2139  72.6886  0.000124287   

                                       se      dse warning loo_scale  
partpooled_model_pooled_data      26.1819        0   False       log  
partpooled_model_partpooled_data  25.2337   32.344   False       log  
partpooled_model_unpooled_data    25.1375  32.9638   False       log

### Compare datasets with different models

In [54]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "unpooled_model_pooled_data": az_unpooled_model_pooled_data, 
            "partpooled_model_pooled_data": az_partpooled_model_pooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo     d_loo    weight  \
unpooled_model_pooled_data      0 -701.455  20.3711         0  0.496582   
pooled_model_pooled_data        1 -702.378  2.06549  0.922622  0.337148   
partpooled_model_pooled_data    2  -703.59  29.7137   2.13495   0.16627   

                                   se      dse warning loo_scale  
unpooled_model_pooled_data    24.8633        0   False       log  
pooled_model_pooled_data      24.9655  2.11963   False       log  
partpooled_model_pooled_data  25.2935  1.85016   False       log

In [55]:
az.compare({"pooled_model_unpooled_data": az_pooled_model_unpooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo     d_loo     weight  \
unpooled_model_unpooled_data      0 -773.176  15.8619         0   0.469666   
pooled_model_unpooled_data        1 -773.488  2.05086  0.311349   0.452417   
partpooled_model_unpooled_data    2 -776.279  26.2139   3.10243  0.0779171   

                                     se      dse warning loo_scale  
unpooled_model_unpooled_data    25.6495        0   False       log  
pooled_model_unpooled_data      25.5891  1.57715   False       log  
partpooled_model_unpooled_data  25.9551  1.84647   False       log

In [56]:
az.compare({"pooled_model_partpooled_data": az_pooled_model_partpooled_data,
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo      weight  \
partpooled_model_partpooled_data    0 -708.151  19.3844        0    0.988806   
unpooled_model_partpooled_data      1  -722.43  24.5418  14.2791  0.00509296   
pooled_model_partpooled_data        2 -725.945  1.98954   17.794  0.00610141   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  25.5329        0   False       log  
unpooled_model_partpooled_data     25.644  5.44499   False       log  
pooled_model_partpooled_data      25.5736  7.08617   False       log

### other stuff

In [50]:
# Save trace.  To load in different notebook, model context and sample data is required.
pm.save_trace(partpooled_model_partpooled_data['trace'], directory = "/home/henry/oaks-thesis/trace/quadratic-pmpd")

'/home/henry/oaks-thesis/trace/quadratic-pmpd'

In [51]:
quadratic_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

In [52]:
%store quadratic_args

Stored 'quadratic_args' (list)
